## Imports

In [1]:
import pandas as pd
import numpy as np
import re

pd.set_option('display.max_columns', None)

In [2]:
df_comments = pd.read_csv('fb_news_comments_1000K_hashed.csv')
df_posts = pd.read_csv('fb_news_posts_20K.csv')

In [3]:
df_posts.head(1)

created_time description  \
0  2017-07-14T14:30:59+0000         NaN   

                                                link  \
0  https://www.facebook.com/bbcnews/videos/101548...   

                                             message       page_id  \
0  We are #LIVE outside the National Rifle Associ...  228735667216   

                          post_id  react_angry  react_haha  react_like  \
0  228735667216_10154890879532217           54          24         993   

   react_love  react_sad  react_wow                 scrape_time  shares  
0         144         12         24  2017-07-14 11:01:24.379857     139

In [4]:
df_comments.head(1)

created_time               from_id             from_name  \
0  2017-07-14T14:43:54+0000  33661642d99eeceeb086  4ca212f16b9f954d5e0a   

                                             message  \
0  We are speaking to NRA supporters as well as W...   

                                post_name  
0  33661642d99eeceeb086_10154890879532217

## Cleaning + making new columns

In [5]:
#Clean date
df_posts['date'] = df_posts['created_time'].str[0:10]
df_posts['date'] = pd.to_datetime(df_posts['date'])

In [6]:
#Clean time
df_posts['time'] = df_posts['created_time'].str[11:19]
df_posts['time'] = pd.to_datetime(df_posts['time'],format="%H:%M:%S")

In [7]:
#Percent angry reacts
df_posts['percent_angry'] = (df_posts['react_angry'] / (df_posts['react_angry'] + df_posts['react_haha'] + df_posts['react_like'] + df_posts['react_love'] + df_posts['react_sad'] + df_posts['react_wow'])) * 100

In [8]:
#Number all reacts
df_posts['all_reacts'] = (df_posts['react_angry'] + df_posts['react_haha'] + df_posts['react_like'] + df_posts['react_love'] + df_posts['react_sad'] + df_posts['react_wow'])

In [9]:
#Make df of posts above 50 reacts (decent exposure) and descriptions
df_posts_big = df_posts[df_posts['all_reacts'] > 50]
df_posts_big = df_posts_big[df_posts_big['message'].notna()]

## Exploration

In [10]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer = TfidfVectorizer(stop_words='english', min_df=5, max_df=0.5, ngram_range=(1, 2))

matrix = vectorizer.fit_transform(df_posts_big.message)
words_df = pd.DataFrame(matrix.toarray(),
                        columns=vectorizer.get_feature_names())
words_df

000  000 mile  000 people   05   07   10  10 000  10 percent  10 years  \
0      0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   
1      0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   
2      0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   
3      0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   
4      0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   
...    ...       ...         ...  ...  ...  ...     ...         ...       ...   
16248  0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   
16249  0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   
16250  0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   
16251  0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   
16252  0.0       0.0         0.0  0.0  0.0  0.0     0.0         0.0       0.0   

       100  100 000  100 days  100 percent  100 years  100th  101   11  11 et  \
0      0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   
1      0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   
2      0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   
3      0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   
4      0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   
...    ...      ...       ...          ...        ...    ...  ...  ...    ...   
16248  0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   
16249  0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   
16250  0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   
16251  0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   
16252  0.0      0.0       0.0          0.0        0.0    0.0  0.0  0.0    0.0   

       11 month  11th   12  12 000  12 hours  12 year  120  126   13  13 year  \
0           0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   
1           0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   
2           0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   
3           0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   
4           0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   
...         ...   ...  ...     ...       ...      ...  ...  ...  ...      ...   
16248       0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   
16249       0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   
16250       0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   
16251       0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   
16252       0.0   0.0  0.0     0.0       0.0      0.0  0.0  0.0  0.0      0.0   

       130   14  14 billion  14 year  140   15  15 000  15 marines  15 year  \
0      0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   
1      0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   
2      0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   
3      0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   
4      0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   
...    ...  ...         ...      ...  ...  ...     ...         ...      ...   
16248  0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   
16249  0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   
16250  0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   
16251  0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   
16252  0.0  0.0         0.0      0.0  0.0  0.0     0.0         0.0      0.0   

       15 years  150        16  16 people   17  1776   18  18 months  18 year  \
0           0.0  0.0  0.000000        0.0  0.0   0.0  0.0 

In [11]:
len(df_posts_big[df_posts_big['percent_angry'] > 30])

2334

### Message + angriness

In [74]:
from sklearn import preprocessing

le = preprocessing.LabelEncoder()
df_posts_big['angry_label'] = le.fit_transform(df_posts_big.percent_angry > 30)
df_posts_big[df_posts_big['angry_label'] == 1].head(1)

created_time description                   link  \
15  2017-07-14T05:21:06+0000              http://bbc.in/2sWnARI   

                                              message       page_id  \
15  Five attacks in north-east London involved cor...  228735667216   

                           post_id  react_angry  react_haha  react_like  \
15  228735667216_10154889722087217          955           6        1368   

    react_love  react_sad  react_wow                 scrape_time  shares  \
15           7        336        192  2017-07-14 11:01:24.379857     537   

         date                time  percent_angry  all_reacts  angry_label  
15 2017-07-14 1900-01-01 05:21:06      33.344972        2864            1

In [13]:
X = words_df
y = df_posts_big.angry_label

In [14]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y)

In [15]:
# LinearSVC: 0.84

# from sklearn.svm import LinearSVC
# clf = LinearSVC(max_iter=10000)
# clf.fit(X_train, y_train)

from sklearn.ensemble import RandomForestClassifier
clf = RandomForestClassifier(n_estimators=10)
clf.fit(X, y)

RandomForestClassifier(n_estimators=10)

In [16]:
clf.score(X_test, y_test)

0.9667814960629921

In [17]:
from sklearn.metrics import confusion_matrix

y_true = y_test
y_pred = clf.predict(X_test)
matrix = confusion_matrix(y_true, y_pred)

label_names = pd.Series(['not angry', 'angry'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

Predicted not angry  Predicted angry
Is not angry                 3463                7
Is angry                      128              466

In [18]:
import eli5

feature_names = list(words_df.columns)
eli5.show_weights(clf, feature_names=feature_names, top=50)

### Comments and angriness

In [28]:
#Turn stuff into strings
df_comments['from_name'] = df_comments['from_name'].astype(str)
df_comments['message'] = df_comments['message'].astype(str)

In [29]:
#Stick comments together and group by post id to allow for join with main csv
df_comments['post_id_for_merge'] = df_comments['post_name'].str.split('_').str[-1].astype(str)
df_aggregated_comments = df_comments.groupby('post_id_for_merge')['message'].agg('|'.join)
df_aggregated_comments = df_aggregated_comments.to_frame()

In [30]:
#Make column to join by in main df
df_posts['post_id_for_merge'] = df_posts['post_id'].str.split('_').str[-1].astype(str)

In [36]:
#Merge
df_new = df_posts.merge(df_aggregated_comments,right_index=True,left_on="post_id_for_merge")

In [45]:
df_new.head(2)

created_time description  \
0  2017-07-14T14:30:59+0000         NaN   
1  2017-07-14T14:20:59+0000               

                                                link  \
0  https://www.facebook.com/bbcnews/videos/101548...   
1                              http://bbc.in/2talMsx   

                                           message_x       page_id  \
0  We are #LIVE outside the National Rifle Associ...  228735667216   
1  UPDATE: \r\n-2 Ukrainian tourists killed in st...  228735667216   

                          post_id  react_angry  react_haha  react_like  \
0  228735667216_10154890879532217           54          24         993   
1  228735667216_10154890968202217          172           8         994   

   react_love  react_sad  react_wow                 scrape_time  shares  \
0         144         12         24  2017-07-14 11:01:24.379857     139   
1          11        783        264  2017-07-14 11:01:24.379857     680   

        date                time  percent_angry  all_reacts  \
0 2017-07-14 1900-01-01 14:30:59       4.316547        1251   
1 2017-07-14 1900-01-01 14:20:59       7.706093        2232   

   post_id_for_merge                                          message_y  \
0  10154890879532217  We are speaking to NRA supporters as well as W...   
1  10154890968202217  I hope it was just a random crime and won't be...   

   angry_label  
0            0  
1            0

In [60]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer = TfidfVectorizer(stop_words='english', min_df=5, max_df=0.5, ngram_range=(1, 2))

matrix = vectorizer.fit_transform(df_new.message_y)

In [61]:
from sklearn import preprocessing

le = preprocessing.LabelEncoder()
df_new['angry_label'] = le.fit_transform(df_new.percent_angry > 30)
df_new[df_new['angry_label'] == 1].head(2)

created_time description                   link  \
15  2017-07-14T05:21:06+0000              http://bbc.in/2sWnARI   
21  2017-07-14T01:40:03+0000              http://bbc.in/2tQZR6N   

                                            message_x       page_id  \
15  Five attacks in north-east London involved cor...  228735667216   
21  So what's in the latest version of the Republi...  228735667216   

                           post_id  react_angry  react_haha  react_like  \
15  228735667216_10154889722087217          955           6        1368   
21  228735667216_10154889223727217          626          70         747   

    react_love  react_sad  react_wow                 scrape_time  shares  \
15           7        336        192  2017-07-14 11:01:24.379857     537   
21          23         28         25  2017-07-14 11:01:24.379857     126   

         date                time  percent_angry  all_reacts  \
15 2017-07-14 1900-01-01 05:21:06      33.344972        2864   
21 2017-07-14 1900-01-01 01:40:03      41.211323        1519   

    post_id_for_merge                                          message_y  \
15  10154889722087217  Standard Nazi tactics. They were fed a daily d...   
21  10154889223727217  Yeah taking healthcare away from the poor and ...   

    angry_label  
15            1  
21            1

In [62]:
X = matrix
y = df_new.angry_label

In [63]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y)

In [64]:
from sklearn.ensemble import RandomForestClassifier
clf = RandomForestClassifier(n_estimators=10)
clf.fit(X, y)

RandomForestClassifier(n_estimators=10)

In [65]:
clf.score(X_test, y_test)

0.980503144654088

In [66]:
from sklearn.metrics import confusion_matrix

y_true = y_test
y_pred = clf.predict(X_test)
matrix = confusion_matrix(y_true, y_pred)

label_names = pd.Series(['not angry', 'angry'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

Predicted not angry  Predicted angry
Is not angry                 4158                1
Is angry                       92              519

In [73]:
import eli5

feature_names = vectorizer.get_feature_names()
eli5.show_weights(clf, feature_names=feature_names, top=50)